In [4]:
import pandas as pd 
import requests
import os
import json

In [1]:
#list of the draft years to pull
year_list = [2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018]

In [2]:
all_url = []
for i in range(10):
    draft_year = year_list[i]
    nhl_url = 'https://statsapi.web.nhl.com/api/v1/draft/'+str(draft_year)
    all_url.append(nhl_url)

In [5]:
draft_data = []

for j in range(10):
    response = requests.get(all_url[j])
    draft_data.append(response.json())

In [6]:
from IPython.display import JSON
JSON(draft_data)

<IPython.core.display.JSON object>

In [7]:
#lists for creation of data frame 
draft_year = []
pick_no = []
team = []
prospect_name = []
prospect_id = []

In [8]:
#create lists from JSON 
for i in range(len(draft_data)):
    for j in draft_data[i]['drafts'][0]['rounds'][0]['picks']:
        draft_year.append(draft_data[i]['drafts'][0]['draftYear'])
        pick_no.append(j['pickOverall'])
        team.append(j['team']['name'])
        prospect_name.append(j['prospect']['fullName'])
        prospect_id.append(j['prospect']['id'])

In [13]:
#get urls for prospect info
all_prospect_url = []
for i in range(len(prospect_id)):
    prospect = prospect_id[i]
    prospect_url = 'https://statsapi.web.nhl.com/api/v1/draft/prospects/'+str(prospect)
    all_prospect_url.append(prospect_url)

In [16]:
#pull prospect data 
prospect_data = []

for j in range(len(all_prospect_url)):
    response = requests.get(all_prospect_url[j])
    prospect_data.append(response.json())

In [17]:
from IPython.display import JSON
JSON(prospect_data)

<IPython.core.display.JSON object>

In [27]:
#lists for creation of data frame 
dob = []
birth_country = []
height = []
weight = []
shoots = []
nhl_id = []
position = []
prospect_category = []
amateur_team = []
amateur_league = []

In [28]:
for i in range(len(prospect_data)):
    dob.append(prospect_data[i]['prospects'][0]['birthDate'])
    birth_country.append(prospect_data[i]['prospects'][0]['birthCountry'])
    height.append(prospect_data[i]['prospects'][0]['height'])
    weight.append(prospect_data[i]['prospects'][0]['weight']) 
    shoots.append(prospect_data[i]['prospects'][0]['shootsCatches'])
    nhl_id.append(prospect_data[i]['prospects'][0]['nhlPlayerId'])
    position.append(prospect_data[i]['prospects'][0]['primaryPosition']['abbreviation'])
    prospect_category.append(prospect_data[i]['prospects'][0]['prospectCategory']['name'])
    amateur_league.append(prospect_data[i]['prospects'][0]['amateurLeague']['name'])
    amateur_team.append(prospect_data[i]['prospects'][0]['amateurTeam']['name'])

In [31]:
#create a data frame with the information 
draft_data = pd.DataFrame(list(zip(draft_year, pick_no, team, prospect_name, prospect_id, dob, birth_country, height,
                                  weight, shoots, nhl_id, position, prospect_category, amateur_league, amateur_team)),
               columns =['draft_year', 'pick_no', 'team', 'prospect_name', 'prospect_id', 'dob', 'birth_country', 'height',
                            'weight', 'shoots', 'nhl_id', 'position', 'prospect_category', 'amateur_league', 'amateur_team'])

In [32]:
draft_data.head()

draft_year  pick_no                 team   prospect_name  prospect_id  \
0        2009        1   New York Islanders    John Tavares        24111   
1        2009        2  Tampa Bay Lightning   Victor Hedman        33799   
2        2009        3   Colorado Avalanche    Matt Duchene         6608   
3        2009        4    Atlanta Thrashers    Evander Kane        12164   
4        2009        5    Los Angeles Kings  Brayden Schenn        21822   

          dob birth_country height  weight shoots   nhl_id position  \
0  1990-09-20           CAN  6' 1"     209      L  8475166        C   
1  1990-12-18           SWE  6' 6"     220      L  8475167        D   
2  1991-01-16           CAN  6' 0"     196      L  8475168        C   
3  1991-08-02           CAN  6' 1"     176      L  8475169        C   
4  1991-08-22           CAN  6' 0"     192      L  8475170        C   

       prospect_category amateur_league amateur_team  
0  North American Skater            OHL       London  
1        European Skater         SWEDEN         Modo  
2  North American Skater            OHL     Brampton  
3  North American Skater            WHL    Vancouver  
4  North American Skater            WHL      Brandon

In [34]:
#remove goalies from data frame 
draft_data = draft_data[draft_data['position'] != 'G']  

In [36]:
#create a csv of the draft information 
#draft_data.to_csv('draft_data.csv')

## Games Played in the NHL 

In [39]:
nhl_id_list = draft_data['nhl_id'].tolist()

In [47]:
nhl_id_list[0]

8475166

In [57]:
#getting NHL data for players to calculate total games played 
all_player_stat_url = []

for i in range(len(nhl_id_list)):
    player_id = nhl_id_list[i]
    player_stat_url = "https://statsapi.web.nhl.com/api/v1/people/"+str(player_id)+"/stats?stats=yearByYear"
    all_player_stat_url.append(player_stat_url)

In [58]:
#pull nhl data
nhl_data = []

for j in range(len(all_player_stat_url)):
    response = requests.get(all_player_stat_url[j])
    nhl_data.append(response.json())

In [59]:
from IPython.display import JSON
JSON(nhl_data)

<IPython.core.display.JSON object>

In [94]:
#save the JSON 
#with open('nhl_data.json', 'w') as json_file:
 #   json.dump(nhl_data, json_file)

In [183]:
player_games_list = []

for player in nhl_data[:]:
    player_games = 0
    player_stats = player['stats']
    player_splits = player_stats[0]['splits']
    i = 0
    for player_split in player_splits:
        i+=1
        if player_split['league']['name'] == 'National Hockey League':
            player_games += player_split['stat']['games']

    player_games_list.append(player_games)

In [184]:
#create a data frame with the information 
nhl_games_data = pd.DataFrame(list(zip(nhl_id_list, player_games_list)),
               columns =['nhl_id', 'nhl_games_played'])

In [185]:
nhl_games_data.head(2)

nhl_id  nhl_games_played
0  8475166              1017
1  8475167               964

In [186]:
#create list to make nhl games played a binary variable 
plus_equal_200 = []
for games in nhl_games_data['nhl_games_played']:
    if games >=200:
        plus_equal_200.append('1')
    elif games < 200:   
        plus_equal_200.append('0')

In [187]:
nhl_games_data['200+games'] = plus_equal_200

In [193]:
nhl_games_data.head(1)

nhl_id  nhl_games_played 200+games
0  8475166              1017         1

## Joining Data 

In [192]:
draft_data.head(1)

draft_year  pick_no                team prospect_name  prospect_id  \
0        2009        1  New York Islanders  John Tavares        24111   

          dob birth_country height  weight shoots   nhl_id position  \
0  1990-09-20           CAN  6' 1"     209      L  8475166        C   

       prospect_category amateur_league amateur_team  
0  North American Skater            OHL       London

In [194]:
#joining tables 
data = pd.merge(draft_data, nhl_games_data,  on = 'nhl_id')
data.head()

draft_year  pick_no                 team   prospect_name  prospect_id  \
0        2009        1   New York Islanders    John Tavares        24111   
1        2009        2  Tampa Bay Lightning   Victor Hedman        33799   
2        2009        3   Colorado Avalanche    Matt Duchene         6608   
3        2009        4    Atlanta Thrashers    Evander Kane        12164   
4        2009        5    Los Angeles Kings  Brayden Schenn        21822   

          dob birth_country height  weight shoots   nhl_id position  \
0  1990-09-20           CAN  6' 1"     209      L  8475166        C   
1  1990-12-18           SWE  6' 6"     220      L  8475167        D   
2  1991-01-16           CAN  6' 0"     196      L  8475168        C   
3  1991-08-02           CAN  6' 1"     176      L  8475169        C   
4  1991-08-22           CAN  6' 0"     192      L  8475170        C   

       prospect_category amateur_league amateur_team  nhl_games_played  \
0  North American Skater            OHL       London              1017   
1        European Skater         SWEDEN         Modo               964   
2  North American Skater            OHL     Brampton               972   
3  North American Skater            WHL    Vancouver               841   
4  North American Skater            WHL      Brandon               845   

  200+games  
0         1  
1         1  
2         1  
3         1  
4         1

In [195]:
#save the data to csv 
#data.to_csv('nhl_data.csv')